In [17]:
substring_to_match = "BH"
input_file_path = "/Users/ted/Documents/RA/RAW_DATA/DOWNLOAD/nibrs-2021/2021_NIBRS_NATIONAL_MASTER_FILE_ENC.txt"
input_file_path = "/Users/ted/Documents/RA/RAW_DATA/DOWNLOAD/FBI/1998/KCNIBR98.DAT"
input_file_path = "/Users/ted/Documents/RA/DATA/FBI/2012/NIBRS12.ENC"

BH_lines = []
# Open the input file in a read mode
with open(input_file_path, 'r', encoding="latin-1") as file:
    # Use a generator to yield only the lines that start with the desired substring
    matching_lines = (line for line in file if line.startswith(substring_to_match))

    # You can iterate over matching_lines or process them as needed
    BH_lines.extend(matching_lines)


In [18]:
BH_lines[2660:3000]

['B109FL0188000\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x0020130905        FGC: FLAGLER COUNTY           FL9D536N         3330080M\n',
 'B109FL0189000\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x0020130304        HP: FLAGLER COUNTY            FL9D534N         3330080M\n',
 'B109FL019DB00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x0020010717        FRANKLIN CO DIV BEVERAGE      FL8D530NFL01900003330085N 20000101\n',
 'B109FL019DL00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x0020010718        FRANKLIN CO CRIM LAW ENF      FL8D530NFL01900003330085N 20000101\n',
 'B109FL019GM00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x0020010717        FRANKLIN CO GAME FWF COM      FL8D530NFL03708003330085N 20000101\n',
 'B109FL019HP00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x0020010717        FRANKLIN HIGHWAY PATROL       FL8D530NFL01990003330085N 20000101\n',
 'B109FL019MP00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x0020010717        FRANKLIN CO MARINE PTL        FL8D530NFL01940003330

In [3]:
import pandas as pd
all_agencies_2021 = pd.DataFrame(
[{"ORI":s[4:13],"POPULATION":int(s[105:114]),"01-06-12 INDICATOR":s[225:227], "NUMBER OF MONTHS REPORTED":int(s[227:229]),"AGENCY ACTIVITY INDICATORS":s[233:269],
  "DATE ORI WENT NIBRS":s[33:41], "AGENCY INACTIVE DATE":s[97:105], "COVERED-BY ORI ":s[79:88], "AGENCY NIBRS FLAG":s[96:97]}  for s in BH_lines]
)
all_agencies_2021

ORI  POPULATION 01-06-12 INDICATOR  NUMBER OF MONTHS REPORTED  \
0      AK0010100      286238                                             0   
1      AK0010200       30598                 01                          5   
2      AK0010300       31874                                             0   
3      AK0010400        8198                 12                         12   
4      AK0010500        5776                 12                         12   
...          ...         ...                ...                        ...   
21468  WY0230000        2318                 12                         12   
21469  WY0230100        3293                 12                         12   
21470  WY0230200        1026                                             0   
21471  WYDI05000           0                 06                         10   
21472  WYWHP0000           0                 01                          4   

                 AGENCY ACTIVITY INDICATORS DATE ORI WENT NIBRS  \
0      NNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNN                       
1      NYNNYNNYNNYNNNNNNNNNNNNNNNNNNNNNNNNN            20210101   
2      NNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNN                       
3      NYNNYNNYNNYNNYNNYNNYNNYNNYNNYNNYNNYN            20210101   
4      NYNNYNNYNNYNNYNNYNNYNNYNNYNNYNNYNNYN            20210101   
...                                     ...                 ...   
21468  NYNNYNNYNNYNNYNNYNNYNNYNNYNNYNNYNNYN            20210101   
21469  NYNNYNNYNNYNNYNNYNNYNNYNNYNNYNNYNNYN            20201201   
21470  NNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNN                       
21471  NYNNYNNYNNYNNYNNYNNYNNYNNYNNYNNNNNNN            20210101   
21472  NNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNN                       

      AGENCY INACTIVE DATE COVERED-BY ORI  AGENCY NIBRS FLAG  
0                                                             
1                                                          A  
2                                                             
3                                                          A  
4                                                          A  
...                    ...             ...               ...  
21468                                                      A  
21469                                                      A  
21470                                                         
21471                                                      A  
21472                                                         

[21473 rows x 9 columns]

In [6]:
all_agencies_2021 = pd.read_parquet("2021_data.pq")
baseline_compare_df = pd.read_csv("/Users/ted/Documents/RA/RAW_DATA/fbi_nibrs_participation_data.csv")

In [ ]:
FBI_data_all_agencies = all_agencies_2021["ORI"].unique()
baseline_data_all_agencies = baseline_compare_df["ori"].unique()
set(FBI_data_all_agencies) - set(baseline_data_all_agencies)

In [8]:
len(FBI_data_all_agencies)

21473

# Merge Coord and Plot

In [11]:
coords = baseline_compare_df[["ori", "agency_name_full","longitude", "latitude"]].rename(columns={"ori":"ORI"})
ori_pop_months_report = coords.merge(right=all_agencies_2021[["ORI", "POPULATION", "NUMBER OF MONTHS REPORTED"]], on="ORI")

In [12]:
import plotly.express as px
import numpy as np

px.scatter_mapbox(
    ori_pop_months_report.query("POPULATION > 10000").assign(size_to_plot = lambda r: np.power(r["POPULATION"], 0.8)),
    lat = "latitude", lon="longitude", size="size_to_plot", color="NUMBER OF MONTHS REPORTED", hover_name="agency_name_full",
    zoom= 2.7,
    color_continuous_scale=[(0,"#f55b5b"),(0.7, "#87c487"), (1,"#a2d5f5")],
    mapbox_style="carto-positron"
)

# BH before 2008:

1. Download BH segment 3
2. for each file, get the txt within DS0003
3. compile code according to a dict

In [19]:
import datareader as dr

NIBRS_RAW_FILES_DIR = 'DATA/FBI'
NIBRS_RAW_FILES = dr.read_NIBRS_file_paths(NIBRS_RAW_FILES_DIR)
NIBRS_RAW_FILES



Subdirectory DATA/FBI/.DS_Store does not contain exactly one file.
Subdirectory DATA/FBI/NIBRS Records Description updated.xlsx does not contain exactly one file.


{1991: PosixPath('DATA/FBI/1991/KCNIBR91.DAT'),
 1992: PosixPath('DATA/FBI/1992/KCNIBR92.DAT'),
 1993: PosixPath('DATA/FBI/1993/KCNIBR93.DAT'),
 1994: PosixPath('DATA/FBI/1994/KCNIBR94.DAT'),
 1995: PosixPath('DATA/FBI/1995/KCNIBR95.DAT'),
 1996: PosixPath('DATA/FBI/1996/KCNIBR96.DAT'),
 1997: PosixPath('DATA/FBI/1997/KCNIBR97.DAT'),
 1998: PosixPath('DATA/FBI/1998/KCNIBR98.DAT'),
 1999: PosixPath('DATA/FBI/1999/KCNIBR99.DAT'),
 2000: PosixPath('DATA/FBI/2000/KCNIBR00.DAT'),
 2001: PosixPath('DATA/FBI/2001/NIBR2001.DAT'),
 2002: PosixPath('DATA/FBI/2002/NIBRS02.ENC'),
 2003: PosixPath('DATA/FBI/2003/NIBRS03.ENC'),
 2004: PosixPath('DATA/FBI/2004/NIBRS04.ENC'),
 2005: PosixPath('DATA/FBI/2005/NIBRS05.ENC'),
 2006: PosixPath('DATA/FBI/2006/NIBRS06.ENC'),
 2007: PosixPath('DATA/FBI/2007/NIBR07.ENC'),
 2008: PosixPath('DATA/FBI/2008/NIBRS08.ENC'),
 2009: PosixPath('DATA/FBI/2009/NIBRS09.ENC'),
 2010: PosixPath('DATA/FBI/2010/NIBRS10.ENC'),
 2011: PosixPath('DATA/FBI/2011/NIBRS11.ENC'),
 20

In [9]:
df_lists = []
for year, file in NIBRS_RAW_FILES.items():
    print(f"Processing {year}")
    bh_reader = dr.converter_factory(year)
    df_lists.append(
        bh_reader(file).assign(year = year)
    )

Processing 1991
Processing 1992
Processing 1993
Processing 1994
Processing 1995
Processing 1996
Processing 1997
Processing 1998
Processing 1999
Processing 2000
Processing 2001
Processing 2002
Processing 2003
Processing 2004
Processing 2005
Processing 2006
Processing 2007
Processing 2008
Processing 2009
Processing 2010
Processing 2011
Processing 2012
Processing 2013
Processing 2014
Processing 2015
Processing 2016
Processing 2017
Processing 2018
Processing 2019
Processing 2020
Processing 2021


In [11]:
import pandas as pd
concat_NIBRS_BH_df = pd.concat(df_lists)

In [20]:
bh_2012 = dr.converter_factory(2012)(NIBRS_RAW_FILES[2012])

In [23]:
all_df = pd.concat([all_df, bh_2012.assign(year = 2012)])

In [25]:
all_df.drop(columns=["INCIDENT NUMBER"]).to_pickle("./DATA/BH.pkl")

# Merge all raw with Baseline

In [26]:
import pandas as pd

bs_df = pd.read_csv("DATA/fbi_nibrs_participation_data.csv")    # baseline
all_df = pd.read_pickle("DATA/BH.pkl")                          # all year

In [27]:
def to_selected_agency_info(df:pd.DataFrame) -> pd.DataFrame:
    coords = df[["ori", "agency_name_full","longitude", "latitude"]].rename(columns={"ori":"ORI"})
    return coords

geo_info = to_selected_agency_info(bs_df)
geo_info

ORI                                agency_name_full   longitude  \
0      AK0010100                     anchorage police department -149.284329   
1      AK0010200                          fairbanks police dept. -146.601909   
2      AK0010300                             juneau police dept. -134.178445   
3      AK0010400                          ketchikan police dept. -131.106685   
4      AK0010500                             kodiak police dept. -153.630606   
...          ...                                             ...         ...   
17113  WY0230000                  weston county sheriff's office -104.570020   
17114  WY0230100                           newcastle police dept -104.570020   
17115  WY0230200                         upton police department -104.570020   
17116  WYDI05000  bu ind aff law enf wind river agcy ft washakie -108.605531   
17117  WYWHP0000                          wyoming highway patrol -104.660395   

        latitude  
0      61.174250  
1      64.691501  
2      58.372910  
3      55.449938  
4      57.553159  
...          ...  
17113  43.846213  
17114  43.846213  
17115  43.846213  
17116  43.055303  
17117  41.292830  

[17118 rows x 4 columns]

In [63]:
def filter_raw_in_geo(df:pd.DataFrame, df_geo:pd.DataFrame) -> pd.DataFrame:
    return df_geo.merge(df, on="ORI", how="left")

def to_plottable_df(df:pd.DataFrame)->pd.DataFrame:
    return (
        df
        .rename(
            columns={
                  "CURRENT POPULATION 1": "POPULATION"
              })
        .assign(
            size_to_plot = lambda r: np.power(r["POPULATION"], 0.8)
        )
        .sort_values(
            by = ["ORI", "year"]
        )
        .astype({
        'NUMBER OF MONTHS REPORTED': 'int8',
        'year':'int32'
    }))[["year", "ORI","agency_name_full", "POPULATION", "size_to_plot", "NUMBER OF MONTHS REPORTED", "latitude", "longitude",]]

df_to_plot = filter_raw_in_geo(all_df, geo_info).pipe(to_plottable_df)
df_to_plot

year        ORI             agency_name_full  POPULATION  \
0       1991  AK0010100  anchorage police department    234571.0   
1       1992  AK0010100  anchorage police department    241565.0   
2       1993  AK0010100  anchorage police department    250720.0   
3       1994  AK0010100  anchorage police department    253667.0   
4       1995  AK0010100  anchorage police department    253500.0   
...      ...        ...                          ...         ...   
500441  2017  WYWHP0000       wyoming highway patrol         0.0   
500442  2018  WYWHP0000       wyoming highway patrol         0.0   
500443  2019  WYWHP0000       wyoming highway patrol         0.0   
500444  2020  WYWHP0000       wyoming highway patrol         0.0   
500445  2021  WYWHP0000       wyoming highway patrol         0.0   

        size_to_plot  NUMBER OF MONTHS REPORTED  latitude   longitude  
0       19779.688846                          0  61.17425 -149.284329  
1       20250.101677                          0  61.17425 -149.284329  
2       20861.771455                          0  61.17425 -149.284329  
3       21057.711831                          0  61.17425 -149.284329  
4       21046.620536                          0  61.17425 -149.284329  
...              ...                        ...       ...         ...  
500441      0.000000                          0  41.29283 -104.660395  
500442      0.000000                          0  41.29283 -104.660395  
500443      0.000000                          0  41.29283 -104.660395  
500444      0.000000                          0  41.29283 -104.660395  
500445      0.000000                          4  41.29283 -104.660395  

[500447 rows x 8 columns]

In [51]:
df_to_plot.groupby(by = ["year"]).count()["ORI"].reset_index()

year    ORI
0   1991  14283
1   1992  14388
2   1993  14510
3   1994  14593
4   1995  14661
5   1996  14884
6   1997  15052
7   1998  15217
8   1999  15363
9   2000  15409
10  2001  15859
11  2002  15931
12  2003  16084
13  2004  16172
14  2005  16273
15  2006  16402
16  2007  16508
17  2008  16755
18  2009  16890
19  2010  17000
20  2011  17117
21  2012  17117
22  2013  17118
23  2014  17118
24  2015  17118
25  2016  17118
26  2017  17117
27  2018  17118
28  2019  17118
29  2020  17118
30  2021  17036

In [74]:
import plotly.express as px
import numpy as np

fig = px.scatter_mapbox(
    df_to_plot.query("`POPULATION` > 50000"),
    lat = "latitude", lon="longitude", size="size_to_plot", color="NUMBER OF MONTHS REPORTED", hover_name="agency_name_full",
    zoom= 3,
    color_continuous_scale=[(0,"#f55b5b"),(0.7, "#87c487"), (1,"#a2d5f5")],
    animation_frame="year",
    mapbox_style="carto-positron"
)
fig.update_layout(height=600, margin={"r":0,"t":20,"l":50,"b":0})

In [61]:
df_to_plot.groupby(by=["year"])["POPULATION"].max()

year
1991    7350023.0
1992    7350023.0
1993    7375097.0
1994    7347257.0
1995    7336224.0
1996    7319546.0
1997    7339594.0
1998    7320477.0
1999    7357745.0
2000    7429263.0
2001    7746511.0
2002    8023018.0
2003    8084693.0
2004    8098066.0
2005    8101321.0
2006    8115690.0
2007    8165001.0
2008    8220196.0
2009    8345075.0
2010    8400907.0
2011    8175133.0
2012    8211875.0
2013    8289415.0
2014    8396126.0
2015    8473938.0
2016    8550861.0
2017          0.0
2018          0.0
2019          0.0
2020          0.0
2021          0.0
Name: POPULATION, dtype: float64

In [62]:
all_df

SEGMENT LEVEL  NUMERIC STATE CODE        ORI DATE ORI WAS ADDED  \
0                B1                 1.0  ALAST0000           19910430   
1                B1                 1.0  AL0010000           19930225   
2                B1                 1.0  AL0010100           19910513   
3                B1                 1.0  AL0010200           19920326   
4                B1                 1.0  AL0010300           19910513   
...             ...                 ...        ...                ...   
22196            B1                52.0  CZ0000500           20130905   
22197            B1                53.0  PRPPR0000           20130903   
22198            B1                55.0  GMTGM0000           20130903   
22199            B1                62.0  VI0010000           20130903   
22200            B1                62.0  VI0010300           20130903   

      DATE ORI WENT NIBRS                       CITY NAME STATE ABBREVIATION  \
0                          MONTGOMERY                                     AL   
1                19910101  BIRMINGHAM                                     AL   
2                19910101  BESSEMER                                       AL   
3                19910101  BIRMINGHAM                                     AL   
4                19910101  MOUNTAIN BROOK                                 AL   
...                   ...                             ...                ...   
22196                      CANAL ZONE                                     CZ   
22197                      PUERTO RICO                                    PR   
22198                      GUAM                                           GM   
22199                      ST. THOMAS                                     VI   
22200                      ST. CROIX                                      VI   

      POPULATION GROUP  COUNTRY DIVISION COUNTRY REGION  ...  \
0                   8D               6.0              3  ...   
1                   9A               6.0              3  ...   
2                    4               6.0              3  ...   
3                   1C               6.0              3  ...   
4                    5               6.0              3  ...   
...                ...               ...            ...  ...   
22196                0               0.0              *  ...   
22197                0               0.0              0  ...   
22198                0               0.0              0  ...   
22199                0               0.0              0  ...   
22200                0               0.0              0  ...   

      AGENCY ACTIVITY INDICATOR 10 AGENCY ACTIVITY INDICATOR 11  \
0                                                                 
1                               Y                            Y    
2                               Y                            Y    
3                               Y                            Y    
4                               Y                            Y    
...                            ...                          ...   
22196                                                             
22197                                                             
22198                                                             
22199                                                             
22200                                                             

      AGENCY ACTIVITY INDICATOR 12  FIPS COUNTY  1 FIPS COUNTY  2  \
0                                                                   
1                               Y               73                  
2                               Y               73                  
3                               Y               73                  
4                               Y               73                  
...                            ...             ...            ...   
22196                                                               
22197                                     